In [ ]:
def traces_figure(run):
    fig = plt.figure(num=1, figsize=(11.5, 9))
    fig.clf()
    
    grid = fig.add_gridspec(ncols=2, nrows=2, hspace=0.4, top=0.93, left=0.1, right=0.95)
    
    inp = fig.add_subplot(grid[0, 0])
    inp.set_title(f'Incident train {run.train_ids[0]}')
    inp.set_ylim(-120, 170)
    
    outp = fig.add_subplot(grid[0, 1])
    outp.set_title(f'Emitted train {run.train_ids[0]}')
    outp.set_ylim(-120, 170)
    
    pulsep = fig.add_subplot(grid[1, 0])
    pulsep.set_title(f'First pulse of train {run.train_ids[0]}');
    
    scanp = fig.add_subplot(grid[1, 1])

    return inp, outp, pulsep, scanp

def pulse_coords(train_pulses):
    return np.arange(train_pulses.shape[1]) + np.cumsum(np.arange(train_pulses.shape[0])+train_pulses.shape[1])[:, None]

def xas_figure(figsize=(9, 4)):
    fig, ax = plt.subplots(num=2, clear=True, ncols=1, nrows=1, figsize=figsize)
    ax.set_xlabel('Photon energy / keV')
    ax.set_ylabel('XAS / arb. u.')
    
    dax = ax.twinx()
    dax.set_ylabel('diffXAS / arb. u.')

    return fig, ax, dax

from IPython.core.display import HTML

import numpy as np
import matplotlib.pyplot as plt

## Note that you may not have access to this proposal!

We'll update this notebook once we have suitable open data available.

In [ ]:
from extra.data import open_run
run = open_run(proposal=3495, run=149)

In [ ]:
run.info()

In [ ]:
run.alias

---

## Separate a run into individual scan steps 

```mermaid
flowchart LR
    scan[Photon energy scan]
    scan
```

In [ ]:
plt.figure(1)
plt.plot(run['FXE_XTD9_MONO/MDL/ACCM_PITCH', 'actualPosition'].series());

The `Scan` component helps splitting data along some scanned value

In [ ]:
from extra.components import Scan
scan = Scan(run.alias['photon-energy'], resolution=9e-4)
scan.info()

In [ ]:
scan.plot()

In [ ]:
scan.steps

---

## Build table pumped and unpumped pulses

```mermaid
flowchart LR
    scan[Photon energy scan]
    pulses[Pump-probe pattern]
    scan --> pulses
```

The `PumpProbePulses` component combines FEL and PPL into a single pulse pattern. Here, every other pulse was pumped beginning with an unpumped pulse.

In [ ]:
from extra.components import PumpProbePulses

pulses = PumpProbePulses(run, pulse_offset=1)
pids = pulses.pulse_ids()
pids

In [ ]:
pids.xs(True, level='ppl')

---

## Load and preprocess digitizer data

```mermaid
flowchart LR
    scan[Photon energy scan]
    pulses[Pump-probe pattern]
    diode[Diode data]
    scan --> pulses --> diode
```

The `AdqRawChannel` component allows to load ADQ traces, apply baseline common mode corrections and reshape to pulse traces.

In [ ]:
from extra.components import AdqRawChannel

in_channel = AdqRawChannel(run, '2_B', pulses=pulses)
out_channel = AdqRawChannel(run, '2_A', pulses=pulses)

HTML('<br>'.join([
     f'Trace shape: ({in_channel.trace_shape},)', f'Trace length: {in_channel.trace_duration:.3g} s',
     f'Sampling rate: {in_channel.sampling_rate:.0f} Hz', f'Sample interval: {in_channel.sampling_period:.3g} s',
     f'Samples per pulse: {in_channel.samples_per_pulse()} samples'])) 

In [ ]:
%%time
in_pulses = in_channel.pulse_data()
out_pulses = out_channel.pulse_data()

In [ ]:
in_pulses

Select all pulses of the first train, and load raw trace for the first train to compare

In [ ]:
in_train0_pulses = in_pulses.sel(trainId=run.train_ids[0])
out_train0_pulses = out_pulses.sel(trainId=run.train_ids[0])

in_train0_full = in_channel.raw_samples_key[0].ndarray()[0]
out_train0_full = out_channel.raw_samples_key[0].ndarray()[0]

In [ ]:
inp, outp, pulsep, scanp = traces_figure(run)

inp.plot(pulse_coords(in_train0_pulses).T, in_train0_pulses.T, lw=0.5)
inp.plot(in_train0_full + 150, lw=0.5)
outp.plot(pulse_coords(out_train0_pulses).T, out_train0_pulses.T, lw=0.5)
outp.plot(out_train0_full + 150, lw=0.5)

pulsep.plot(in_pulses.isel(pulse=0), label='Incident')
pulsep.plot(out_pulses.isel(pulse=0), label='Emitted')
pulsep.legend()

scan.plot(ax=scanp);

---

## Combine to XAS signal

```mermaid
flowchart LR
    scan[Photon energy scan]
    pulses[Pump-probe pattern]
    diode[Diode data]
    xas[Construct XAS signal]
    scan --> pulses --> diode --> xas
```

For both in and out signal, select pulses according to whether they're pumoped or not, pick a signal ROI around the peaks, then integrate.

In [ ]:
in_pumped = in_pulses.sel(fel=True, ppl=True, sample=np.s_[2920:3150]).groupby('trainId').mean(...)
in_unpumped = in_pulses.sel(fel=True, ppl=False, sample=np.s_[2920:3150]).groupby('trainId').mean(...)

out_pumped = out_pulses.sel(fel=True, ppl=True, sample=np.s_[2920:3150]).groupby('trainId').mean(...)
out_unpumped = out_pulses.sel(fel=True, ppl=False, sample=np.s_[2920:3150]).groupby('trainId').mean(...)

In [ ]:
in_pumped

Bin the intenstiy ratios of all trains by their mono position.

In [ ]:
pumped_scan = scan.bin_by_steps(out_pumped / in_pumped)
unpumped_scan = scan.bin_by_steps(out_unpumped / in_unpumped)

### Plotting the results

In [ ]:
fig, ax, dax = xas_figure()

ax.plot(scan.positions, pumped_scan, '.-', label='pumped', lw=1)
ax.plot(scan.positions, unpumped_scan, '.-', label='unpumped', lw=1)
dax.plot(scan.positions, pumped_scan - unpumped_scan, '.--', c='C2', label='diff', alpha=0.4, lw=1)

fig.legend(loc=(0.765, 0.76), fontsize='small');